In [ ]:
import re
import requests
from bs4 import BeautifulSoup
from lxml import etree
import pandas as pd

def teacher_data_get(url):
    
    txt = []
    r = requests.get(url)
    r.raise_for_status()
    demo = r.text
    soup = BeautifulSoup(demo,'html.parser')
    soup = soup.div.children
    for i in soup:
        txt.append(i)
        
    first_txt = txt[3];a = str(first_txt)
    second_txt = first_txt.find_all('div', "ne_main_R");b = str(second_txt)
    
    pre = re.compile('>(.*?)<')
    info = pre.findall(b)
    
    info_ = []
    for i in range(len(info)):
        if len(info[i]) > 1 or info[i]=='：':
            info_.append(info[i])
    
    info__ = {'姓　　名':'','性　　别':'','出生年月':'','政治面貌':''
              ,'毕业院校':'','毕业专业':'','职　　务':'','职　　称':''
              ,'联系方式':'','自我简介':'','科研成果':''}
    s1 = ''    
    
    for i in range(len(info_)):
        #提取基本信息
        if info_[i] == '姓　　名':
            info__['姓　　名'] = info_[i+1]
        elif info_[i] == '​姓　　名':
            info__['姓　　名'] = info_[i+1]
        elif info_[i] == '姓　名':
            name = info_[i+1] + info_[i+2]
            info__['姓　　名'] = name
        elif info_[i] == '姓　　名：赵玉洁':
            info__['姓　　名'] = '赵玉洁'
        elif info_[i] == '​Name: Badar Nadeem Ashraf':
            info__['姓　　名'] = 'Badar Nadeem Ashraf'
        elif info_[i] == '名：':
            info__['姓　　名'] = '杨超'
        if info_[i] == '性　　别' or info_[i] == '　　性　别':
            info__['性　　别'] = info_[i+1]
        if info_[i] == '性　　别：女' :
            info__['性　　别'] = '女'
        if info_[i] == 'Sex: Male' :
            info__['性　　别'] = 'Male'
        if info_[i] == '别：' :
            info__['性　　别'] = '男 '
        if info_[i] == '出生年月' or info_[i] == '　　出生年月' or info_[i] == '出生年月：':
            info__['出生年月'] = info_[i+1]
        if info_[i] == '出生':
            info__['出生年月'] = '1986.08'
        if info_[i] == '政治面貌' or info_[i] == '　　政治面貌':
            info__['政治面貌'] = info_[i+1]
        if info_[i] == '毕业院校' or info_[i] == '　　毕业院校':
            info__['毕业院校'] = info_[i+1]
        if info_[i] == '毕业院校：复旦大学':
            info__['毕业院校'] = '复旦大学'
        if info_[i] == '业院':
            info__['毕业院校'] = '西南财经大学'
        if info_[i] == 'Graduated: Huazhong University of Science and Technology':
            info__['毕业院校'] = 'Huazhong University of Science and Technology'
        if info_[i] == '毕业专业' or info_[i] == '　　毕业专业':
            info__['毕业专业'] = info_[i+1]
        if info_[i] == '职　　务' or info_[i] == '　　职　务':
            info__['职　　务'] = info_[i+1]
        if info_[i] == 'Duties: Teaching/Research/Research supervision':
            info__['职　　务'] = 'Teaching/Research/Research supervision'
        if info_[i] == '职　　称' or info_[i]=='职称：':
            info__['职　　称'] = info_[i+1]
        if info_[i] == '职　　称：副教授':
            info__['职　　称'] = '副教授'
        if info_[i] == 'Job title: Associate Professor':
            info__['职　　称'] = 'Associate Professor'
        if info_[i] == '　　职　称':
            work = info_[i+1] + info_[i+2]
            info__['职　　称'] = work
        if info_[i] == '联系方式' or info_[i] == '邮       箱' :
            info__['联系方式'] = info_[i+1]
        if info_[i] == '邮    箱：':
            info__['联系方式'] = info_[i+1]
        if info_[i] == '邮    箱：verg0601@126.com':
            info__['联系方式'] = 'verg0601@126.com'
        if info_[i] == 'Email: ':
            info__['联系方式'] = 'badar@jxufe.edu.cn'
        if info_[i] == '电子邮箱：':
            info__['联系方式'] = '826594365@qq.com'
        
        #提取自我简介
        if info_[i] == '自我简介' or info_[i] == '一、基本情况' or info_[i] == '​自我简介' or info_[i] == 'badar@jxufe.edu.cn' or info_[i] == '硕士生导师':
            info__['自我简介'] = []
            k = i
            while info_[i+1] != '科研成果' and info_[i+1] != '代表性论文' and info_[i+1] != '三、主要成果'  and info_[i+1] != '　　四、科研成果' and info_[i+1] != '3.Major Research Publications':
                i += 1
                s1 += info_[i]
            i = k
            info__['自我简介'].append(s1)
        
        #提取科研成果
        s1 = ''
        if info_[i] == '科研成果' or info_[i] == '代表性论文' or info_[i] == '三、主要成果'  or info_[i] == '　　四、科研成果' or info_[i] == '3.Major Research Publications':
            info__['科研成果'] = []
            k = i
            while i+1 < len(info_):
                i += 1
                s1 += info_[i]
            info__['科研成果'].append(s1)
    return info__

if __name__ == '__main__':
    t_url = 'http://finance.jxufe.edu.cn/news-list-shuodao-{}.html'
    r_text = requests.get(t_url.format(1)).text
    html = etree.HTML(r_text)
    num = html.xpath('//div[@class="bd_listabc"]//p/span[@class="num"]/text()')[0]
    page_num = int(re.findall(r".+/(\d)页", num, re.DOTALL)[0])
    INFO = []
    for i in range(1, page_num+1):
        if i >= 2:
            r_text = requests.get(t_url.format(i)).text
            html = etree.HTML(r_text)
        urls = html.xpath('//div[@class="bd_listabc"]//li//div[@class="textlist"]/a/@href')
        for url in urls:
            info = teacher_data_get(url)
            INFO.append(info)
    
    F_INFO = pd.DataFrame(INFO)

In [2]:
F_INFO

出生年月                 姓　　名  性　　别      政治面貌              毕业专业  \
0             Badar Nadeem Ashraf  Male                               
1          ：                  ：曹邓    ：女     ：中共党员              ：管理学   
2          ：                 ：陈春霞    ：女       ：群众              ：金融学   
3          ：                 ：陈家洪    ：男     ：中共党员     ：经济统计（证券研究方向）   
4          ：                 ：冯凌秉    ：男         ：              ：统计学   
5          ：                 ：桂荷发    ：男     ：民进会员              ：金融学   
6          ：                 ：胡少勇    ：男     ：中共党员              ：精算学   
7          ：                 ：胡援成    ：男       ：党员              ：金融学   
8          ：                 ：胡志军    ：男     ：中共党员            ：数量经济学   
9    ：1980.9                 ：蒋崇辉    ：男     ：中共党员  ：管理科学与工程（金融工程方向）   
10         ：                 ：李思敏    ：男     ：中共党员                 ：   
11         ：                 ：刘金凤    ：女         ：                 ：   
12         ：                 ：刘兴华    ：男     ：中共党员             ：世界经济   
13         ：                 ：吕江林    ：男     ：中共党员              ：经济学   
14  ：1974年7月                 ：闵晓平    ：男  ：中国民主促进会          ：管理科学与工程   
15         ：                 ：钱建豪    ：男         ：            ：经济学博士   
16         ：                  ：潜力    ：男         ：              ：金融学   
17         ：                  ：寿晖    ：男         ：                 ：   
18  ：1969.11                 ：舒海棠    ：女     ：中共党员              ：金融学   
19         ：                 ：孙爱琳    ：女     ：中共党员            ：政治经济学   
20         ：                  ：汪洋    ：男     ：中共党员              ：金融学   
21         ：                  ：王辉    ：男     ：中共党员              ：财政学   
22         ：                 ：王清生    ：男       ：群众         ：概率论与数理统计   
23         ：                 ：吴伟军    ：男     ：中共党员              ：经济学   
24         ：                  ：严武    ：男       ：党员              ：经济学   
25   1986.08                   杨超    男                                
26         ：                  ：杨荣    ：女     ：中共党员              ：金融学   
27         ：                 ：杨玉凤    ：女     ：民主党派              ：金融学   
28      1984                  赵玉洁     女                               
29         ：                 ：邹朋飞    ：男       ：群众              ：金融学   
30         ：                 ：曾鸿志    ：男       ：党员          ：投资经济管理学   
31         ：                 ：王金佑    ：男         ：            ：经济学硕士   

                                             毕业院校  \
0   Huazhong University of Science and Technology   
1                                         ：江西财经大学   
2                                         ：江西财经大学   
3                                         ：江西财经大学   
4                                       ：澳大利亚国立大学   
5                                         ：中国人民大学   
6                                         ：华东师范大学   
7                                           ：厦门大学   
8                                         ：上海财经大学   
9                                         ：电子科技大学   
10                                              ：   
11                                              ：   
12                                          ：厦门大学   
13                                        ：中南财经大学   
14                                        ：上海交通大学   
15                                              ：   
16                                        ：西安交通大学   
17                                              ：   
18                                        ：江西财经大学   
19                                          ：浙江大学   
20                                        ：上海财经大学   
21                                        ：江西财经大学   
22                                          ：云南大学   
23                                        ：江西财经大学   
24                                        ：江西财经大学   
25                                         西南财经大学   
26                                        ：江西财经大学   
27                                        ：江西财经大学   
28                                           复旦大学   
29                                          ：暨南大学   
30                   